## Event Search Example 1

### Example code to search for occultations meeting requested criteria

Revisions:

    2023 Jun 12 - rfrench - original version


In [12]:
from astropy.table import Table
from astropy.time import Time
import numpy as np
import os

program  = 'EventSearchExample1.py'

# Modify this line to point to the path to the local copy of the SOM directory 
# Be sure to include the trailing slash /

# This is the correct SOM_path if the program is run in its default path:
# SOM/doc/EventSearchExample1.py

SOM_path = '../'
OutputFile  = 'EventSearchExample1.out'
    
# Example 1 
#
# run options:
#    ListSummaryFiles 
#       (=True to list the names of summary pdf files for identified events)
#    OpenSummaryFiles 
#       (=True to use OS command to display summary pdf files for identified events)
#    DisplayOutputFile 
#       (=True to display contents of output file with results of search)
#    DetailedOutput
#        (=True to list contents of data table read from Machine Readable file and summary *.txt file)
#    verbose
#        (=True for informative progress report)
# event search specifications:
# Find all predicted occultations by selected
#    Targets
# with corresponding K magnitude upper limits
#    Kmaglims
# visible between specified dates
#    UTCmin, UTCmax
# in selected regions
#    RequestedRegions

ListSummaryFiles = True # set to False to suppress listing of summary pdf
OpenSummaryFiles = True # set to True if "open *.pdf" is a legal OS command
DisplayOutputFile = True # set to False to suppress display of contents of output file
DetailedOutput = True # quantities available in data table from Machine Readable file and summary *.txt file
verbose = True # if True, then list all quantities in the data table

# specify list of targets to search

Targets = ['Jupiter','Saturn','Uranus','Neptune','Titan','Triton']

# specify corresponding upper limits on K magnitude

Kmaglims = [5, 8, 10.9, 11, 7, 15]

# specify date range for search (between 2023-01-01 and 2050-01-01)

UTCmin = '2024-01-01'
UTCmax = '2030-01-01'

# list of available region codes and abbreviated names

RegionCodes = ['NAM','ENA','SAF','SAM','OCN','EAS']
RegionNames = \
 ['N. Am.','Eur.&N.Afr.','S. Afr.','S. Am.','Oceania','E. Asia']

# Select which regions to use for this search

RequestedRegions= [True,True,True,True,True,True]

# END OF USER INPUT

f = open(OutputFile, 'w')
print("Results of ",program,file=f)

count = 0
for RegionName,RequestedRegion in zip(RegionNames,RequestedRegions):
    if RequestedRegion == False:
        continue
    if count == 0 :
        Regionlist = RegionName
    else:
        Regionlist = Regionlist + ', '+RegionName
    count = count + 1

# convert from requested date range to Julian dates

JDmin = Time(UTCmin,format='iso',scale='utc').jd
JDmax = Time(UTCmax,format='iso',scale='utc').jd

# for each target...
first = True
for Target,Kmaglim in (zip(Targets,Kmaglims)):
    inMRfile = SOM_path+'tables/' +Target+'/'+Target+'_predictions_MR.txt'
    data = Table.read(inMRfile, format="ascii.cds")
    if verbose:
        print("MR file:",inMRfile)
    if DetailedOutput and first:
        print('Available contents of data array from MR file:',file=f)
        print(data.info,file=f)
        first = False

        # search for requested events...

    Lmatch = np.where((data['JD'] >= JDmin) & (data['JD'] <= JDmax)
                 & (data['KMAG']<=Kmaglim))

    # determine if ring or planet event is visible from a given region

    print("------------------------------------------------------------------------------",file=f)
    print("Results of search for occultations by",Target,"between",UTCmin,"and",UTCmax,file=f)
    print("K magnitude limit",Kmaglim,file=f)
    print('Visible from ',Regionlist,file=f)
    print(' ',file=f)

    data_ = data[Lmatch]
    total = 0
    for i in range(len(data_)):
        data_i = data_[i]
        visible = ''
        count = 0
        EventFiles= ''
        for RequestedRegion,RegionCode,RegionName in \
            zip(RequestedRegions,RegionCodes,RegionNames):
            if RequestedRegion is False:
                continue
        # confirm that a ring or planet event is visible from this region
            if (data_i[RegionCode+'_N_RINGOCCS'] >0) or (data_i[RegionCode+'_N_TARGETOCCS']>0):
                if count >0:
                    char=', '
                else:
                    char=''
                visible = visible+char+RegionName 
                count = count + 1
                total = total + 1
# An event has been found. List and/or open the summary file if requested
                if count == 1 and (ListSummaryFiles or OpenSummaryFiles):
                    EventSummaryPDFFile = SOM_path + data_i['SUMMARY_PDF'][4:]
                    if OpenSummaryFiles:
                        command = 'open '+EventSummaryPDFFile
                        os.system(command)
                    espdf = EventSummaryPDFFile
                    EventSummaryTextFile = espdf[0:len(espdf)-3]+'txt'
                    with open(EventSummaryTextFile) as ff:
                        contents = ff.read()
                        print(contents,file=f)
        if count >0:
                if verbose:
                    print('  '+data_i['UTC_CA'],f'{data_i["EVENTTYPE"]:<{7}}',\
                      'K=',data_i['KMAG'],'is visible from',visible)
                print('  '+data_i['UTC_CA'],f'{data_i["EVENTTYPE"]:<{7}}',\
                      'K=',data_i['KMAG'],'is visible from',visible,file=f)

                if ListSummaryFiles:
                    print(' ',file=f)
                    print('  Event summary PDF file:',file=f)
                    print(EventSummaryPDFFile,file=f)
                    print('  Event summary text file:',file=f)
                    print(EventSummaryTextFile,file=f) 
                    print(' ',file=f)

    if total == 0:
        print('No events found with requested conditions',file=f)
    print(" ",file=f)
f.close()
if DisplayOutputFile:
    print('********** Contents of ',OutputFile,' ****************')
    with open(OutputFile) as f:
        contents = f.read()
        print(contents)

MR file: ../tables/Jupiter/Jupiter_predictions_MR.txt
  2027-02-22 11:12:09.02 Pgt     K= 4.926 is visible from N. Am., Oceania, E. Asia
MR file: ../tables/Saturn/Saturn_predictions_MR.txt
  2024-08-06 17:12:21.22 PgtRgt  K= 7.716 is visible from N. Am., Oceania, E. Asia
  2029-07-19 00:57:19.09 PgtRgt  K= 7.241 is visible from Eur.&N.Afr., S. Afr., E. Asia
MR file: ../tables/Uranus/Uranus_predictions_MR.txt
  2026-07-21 02:13:50.22 PgtRgt  K= 10.802 is visible from Eur.&N.Afr., S. Afr.
MR file: ../tables/Neptune/Neptune_predictions_MR.txt
  2024-10-09 00:36:23.19 PgtRgt  K= 9.068 is visible from N. Am., Eur.&N.Afr., S. Afr., S. Am.
MR file: ../tables/Titan/Titan_predictions_MR.txt
  2029-03-04 02:37:38.25 Pt      K= 6.151 is visible from N. Am.
MR file: ../tables/Triton/Triton_predictions_MR.txt
  2029-06-11 05:23:26.00 Pt      K= 10.259 is visible from Eur.&N.Afr.
********** Contents of  EventSearchExample1.out  ****************
Results of  EventSearchExample1.py
Available contents o